In [2]:
import os
import numpy as np
from tensorflow.keras.preprocessing import image_dataset_from_directory
from tensorflow.random import set_seed

file_path = "/dvntn9yhd2-1/Covid19-Pneumonia-Normal Chest X-Ray Images Dataset"

set_seed(42)

BATCH_SIZE = 64
IMAGE_SIZE = (128, 128)

dataset = image_dataset_from_directory(
    directory=os.getcwd() + file_path,
    batch_size=BATCH_SIZE,
    color_mode='grayscale',
    image_size=IMAGE_SIZE,
    # rescale=1/255,
    shuffle=True,
    seed=42
)

Found 5228 files belonging to 3 classes.


In [3]:
import tensorflow

In [4]:
classes  = dataset.class_names
classes

['COVID', 'NORMAL', 'PNEUMONIA']

In [5]:
for image_batch, labels_batch in dataset:
    print(image_batch.shape)
    print(labels_batch.shape)
    break

(64, 128, 128, 1)
(64,)


In [6]:
def get_dataset_partitions_tf(ds, train_split=0.8, val_split=0.1, test_split=0.1, shuffle=True, shuffle_size=1000, seed=42):
    assert (train_split + test_split + val_split) == 1

    ds_size = len(ds)

    if shuffle:
        ds = ds.shuffle(shuffle_size, seed=seed)

    train_size = int(train_split * ds_size)
    val_size = int(val_split * ds_size)

    train_set = ds.take(train_size)
    val_set = ds.skip(train_size).take(val_size)
    test_set = ds.skip(train_size).skip(val_size)

    return train_set, val_set, test_set

train_set, val_set, test_set = get_dataset_partitions_tf(dataset)

print(f"Train size: {len(train_set)} \nTest size: {len(test_set)} \nVal size: {len(val_set)}")

Train size: 65 
Test size: 9 
Val size: 8


In [7]:
os.environ["CUDA_VISIBLE_DEVICES"] = "1"

In [8]:
from tensorflow.keras import backend as K

In [9]:
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Rescaling, Conv2D, MaxPooling2D, Flatten, Dense, Dropout
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.losses import SparseCategoricalCrossentropy
import pickle

# Model
Hist_acc_train = []
Hist_acc_val   = []

Hist_loss_train = []
Hist_loss_val   = []
save_path       = os.getcwd() + "/Hasil_RBL/"
k = 119
for conv_quantity in range (4+4,33):
    for dense_quantity in range (4,33):
        # Clear the current session
        K.clear_session()

        set_seed(42)

        num_classes = len(classes)

        model = Sequential([
            Rescaling(1./255),
            Conv2D(conv_quantity, 3, activation='relu'),
            MaxPooling2D(),
            Conv2D(conv_quantity, 3, activation='relu'),
            MaxPooling2D(),
            Flatten(),
            Dropout(0.1),
            Dense(dense_quantity, activation='relu'),
            Dense(3, activation='softmax')
        ])

        model.compile(
            optimizer=Adam(),
            loss=SparseCategoricalCrossentropy(),
            metrics=['accuracy'])


        set_seed(42)
        EPOCHS = 40

        history = model.fit(
            train_set,
            batch_size=BATCH_SIZE,
            validation_data=val_set,
            epochs=EPOCHS
        )

        with open(f'{save_path}model{k+1}.pkl', 'wb') as file:

            # A new file will be created
            pickle.dump(model, file)

        with open(f'{save_path}Hist_loss_train {k+1}.pkl', 'wb') as file:

            # A new file will be created
            pickle.dump(history.history['loss'], file)

        with open(f'{save_path}Hist_loss_val {k+1}.pkl', 'wb') as file:

            # A new file will be created
            pickle.dump(history.history['val_loss'], file)

        with open(f'{save_path}Hist_acc_train {k+1}.pkl', 'wb') as file:

            # A new file will be created
            pickle.dump(history.history['accuracy'], file)

        with open(f'{save_path}Hist_acc_val {k+1}.pkl ', 'wb') as file:

            # A new file will be created
            pickle.dump(history.history['val_accuracy'], file)

        k = k + 1
        print(k)


Epoch 1/40
65/65 [==============================] - 16s 49ms/step - loss: 0.8903 - accuracy: 0.5408 - val_loss: 0.7906 - val_accuracy: 0.6484
Epoch 2/40
65/65 [==============================] - 3s 26ms/step - loss: 0.7833 - accuracy: 0.6322 - val_loss: 0.7480 - val_accuracy: 0.6230
Epoch 3/40
65/65 [==============================] - 3s 24ms/step - loss: 0.7457 - accuracy: 0.6387 - val_loss: 0.7111 - val_accuracy: 0.6699
Epoch 4/40
65/65 [==============================] - 2s 22ms/step - loss: 0.7243 - accuracy: 0.6481 - val_loss: 0.7330 - val_accuracy: 0.6504
Epoch 5/40
65/65 [==============================] - 2s 21ms/step - loss: 0.6961 - accuracy: 0.6478 - val_loss: 0.6528 - val_accuracy: 0.7031
Epoch 6/40
65/65 [==============================] - 2s 20ms/step - loss: 0.6791 - accuracy: 0.6582 - val_loss: 0.6788 - val_accuracy: 0.6582
Epoch 7/40
65/65 [==============================] - 2s 20ms/step - loss: 0.6572 - accuracy: 0.6522 - val_loss: 0.6600 - val_accuracy: 0.7031
Epoch 8/40
6

INFO:tensorflow:Assets written to: ram://002259fd-0e17-4aff-bd96-2692dbbb5b32/assets


INFO:tensorflow:Assets written to: ram://002259fd-0e17-4aff-bd96-2692dbbb5b32/assets


120
Epoch 1/40
65/65 [==============================] - 3s 26ms/step - loss: 0.7236 - accuracy: 0.7221 - val_loss: 0.3391 - val_accuracy: 0.8887
Epoch 2/40
65/65 [==============================] - 2s 25ms/step - loss: 0.2816 - accuracy: 0.8973 - val_loss: 0.2284 - val_accuracy: 0.9121
Epoch 3/40
65/65 [==============================] - 2s 23ms/step - loss: 0.2216 - accuracy: 0.9196 - val_loss: 0.1974 - val_accuracy: 0.9277
Epoch 4/40
65/65 [==============================] - 2s 20ms/step - loss: 0.1807 - accuracy: 0.9346 - val_loss: 0.1591 - val_accuracy: 0.9473
Epoch 5/40
65/65 [==============================] - 2s 21ms/step - loss: 0.1679 - accuracy: 0.9406 - val_loss: 0.1693 - val_accuracy: 0.9277
Epoch 6/40
65/65 [==============================] - 2s 20ms/step - loss: 0.1510 - accuracy: 0.9437 - val_loss: 0.1245 - val_accuracy: 0.9531
Epoch 7/40
65/65 [==============================] - 2s 20ms/step - loss: 0.1411 - accuracy: 0.9490 - val_loss: 0.1275 - val_accuracy: 0.9472
Epoch 8/4

INFO:tensorflow:Assets written to: ram://bc622281-f3f9-487f-a43f-de040d9586b0/assets


...

INFO:tensorflow:Assets written to: ram://e7976797-744e-49dc-88eb-1be0b756d0c8/assets


843
Epoch 1/40
65/65 [==============================] - 6s 49ms/step - loss: 0.4776 - accuracy: 0.8135 - val_loss: 0.2349 - val_accuracy: 0.9219
Epoch 2/40
65/65 [==============================] - 5s 51ms/step - loss: 0.2250 - accuracy: 0.9143 - val_loss: 0.2427 - val_accuracy: 0.9062
Epoch 3/40
65/65 [==============================] - 5s 52ms/step - loss: 0.1670 - accuracy: 0.9423 - val_loss: 0.1770 - val_accuracy: 0.9355
Epoch 4/40
65/65 [==============================] - 5s 48ms/step - loss: 0.1523 - accuracy: 0.9435 - val_loss: 0.1881 - val_accuracy: 0.9453
Epoch 5/40
65/65 [==============================] - 5s 48ms/step - loss: 0.1235 - accuracy: 0.9555 - val_loss: 0.1135 - val_accuracy: 0.9590
Epoch 6/40
65/65 [==============================] - 5s 49ms/step - loss: 0.1112 - accuracy: 0.9608 - val_loss: 0.0977 - val_accuracy: 0.9668
Epoch 7/40
65/65 [==============================] - 5s 48ms/step - loss: 0.0979 - accuracy: 0.9647 - val_loss: 0.0667 - val_accuracy: 0.9805
Epoch 8/4

INFO:tensorflow:Assets written to: ram://12a0cd22-63b6-4086-a89f-d367bd0c1709/assets


INFO:tensorflow:Assets written to: ram://12a0cd22-63b6-4086-a89f-d367bd0c1709/assets


844


In [1]:
print(history)

NameError: name 'history' is not defined

In [ ]:
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Rescaling, Conv2D, MaxPooling2D, Flatten, Dense, Dropout
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.losses import SparseCategoricalCrossentropy

set_seed(42)

num_classes = len(classes)

model = Sequential([
    Rescaling(1./255),
    Conv2D(32, 3, activation='relu'),
    MaxPooling2D(),
    Conv2D(32, 3, activation='relu'),
    MaxPooling2D(),
    Flatten(),
    Dropout(0.1),
    Dense(128, activation='relu'),
    Dense(2, activation='softmax')
])

In [ ]:
model.compile(
    optimizer=Adam(),
    loss=SparseCategoricalCrossentropy(),
    metrics=['accuracy'])

In [1]:
# Create EarlyStopping callback
from tensorflow.keras.callbacks import EarlyStopping

set_seed(42)

early_stopping = EarlyStopping(monitor='val_loss', patience=3, restore_best_weights=True)
EPOCHS = 5

history = model.fit(
    train_set,
    batch_size=BATCH_SIZE,
    validation_data=val_set,
    verbose=1,
    epochs=EPOCHS,
    callbacks=[early_stopping]
)

NameError: name 'set_seed' is not defined

In [ ]:
# Create EarlyStopping callback
from tensorflow.keras.callbacks import EarlyStopping

set_seed(42)

early_stopping = EarlyStopping(monitor='val_loss', patience=3, restore_best_weights=True)
EPOCHS = 5

history = model.fit(
    train_set,
    batch_size=BATCH_SIZE,
    validation_data=val_set,
    verbose=1,
    epochs=EPOCHS,
    callbacks=[early_stopping]
)

In [ ]:
model.summary()

In [ ]:
history.history.keys()

In [ ]:
import matplotlib.pyplot as plt

plt.figure()
plt.plot(range(EPOCHS), history.history['loss'], label='Training Loss', marker='.')
plt.plot(range(EPOCHS), history.history['val_loss'], label='Validation Loss', marker='.')
plt.legend(title="Loss")
plt.title('Training and Validation Loss')
plt.show()

plt.figure()
plt.plot(range(EPOCHS), history.history['accuracy'], label='Training Accuracy', marker='.')
plt.plot(range(EPOCHS), history.history['val_accuracy'], label='Validation Accuracy', marker='.')
plt.legend(title="Accuracy")
plt.title('Training and Validation Accuracy')
plt.show()

In [ ]:
from tensorflow.keras.utils import img_to_array
from tensorflow import expand_dims

def make_prediction(model, img):
    img_array = img_to_array(img)
    img_array = expand_dims(img_array, 0)

    prediction_probability = model.predict(img_array)

    # predicted_class = classes[np.argmax(predictions[0])]
    predicted_class = np.argmax(prediction_probability[0])
    # confidence = round(100 * (np.max(predictions[0])), 4)

    return prediction_probability[0].tolist(), predicted_class

In [ ]:
test_prediction_probability = []
test_predicted_class = []
test_predicted_class_one_hot = np.array([[0,0,0,0] for _ in range(640)])
test_actual_class = []
test_actual_class_one_hot = np.array([[0,0,0,0] for _ in range(640)])

j = 0
for images, labels in test_set:
    for i in range(len(images)):
        prediction_probability, predicted_class = make_prediction(model, images[i].numpy())
        test_prediction_probability.append(prediction_probability)
        test_predicted_class.append(predicted_class)
        test_actual_class.append(labels[i].numpy())

        # actual_class = classes[labels[i]]

In [ ]:
# accuracy

acc_list = np.array([int(test_actual_class[i] == test_predicted_class[i]) for i in range(len(test_actual_class))])
print(f"accuracy_score: {np.mean(acc_list) * 100 :.4f}%")

In [ ]:
import matplotlib.pyplot as plt
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay
from sklearn.model_selection import train_test_split

cm = confusion_matrix(test_actual_class, test_predicted_class)
disp = ConfusionMatrixDisplay(confusion_matrix=cm,
                              display_labels=classes)
fig, ax = plt.subplots(figsize=(10,10))
disp.plot(ax=ax)
plt.title('CNN Confusion Matrix')
plt.show()
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay
from sklearn.model_selection import train_test_split

cm = confusion_matrix(test_actual_class, test_predicted_class)
disp = ConfusionMatrixDisplay(confusion_matrix=cm,
                              display_labels=classes)
fig, ax = plt.subplots(figsize=(10,10))
disp.plot(ax=ax)
plt.title('CNN Confusion Matrix')
plt.show()

In [ ]:
first_layer = model.layers[1].get_weights()[0].reshape(3,3,32)

In [ ]:
model.layers[1]

In [ ]:
# plot first convolution matrix

fig, ax = plt.subplots(4,8,figsize=(20, 8))
ax = ax.flatten()
i = 0
for a in ax:
    a.imshow(first_layer[:,:,i], interpolation='nearest', cmap ='gray', aspect='auto', vmin = min(first_layer.flatten()), vmax = max(first_layer.flatten()))
    i += 1
    a.set_xticks([])
    a.set_yticks([])

In [ ]:
# image after first convolution

from keras.models import Model
from matplotlib import pyplot

alz = Model(inputs=model.inputs, outputs=model.layers[1].output)

fig, axes = plt.subplots(4,8,figsize=(20, 8))
axes = axes.flatten()

# get feature map for first hidden layer
feature_maps = alz.predict(images)
# plot all 64 maps in an 8x8 squares
ix = 0
for ax in axes:
    # specify subplot and turn of axis
    ax.set_xticks([])
    ax.set_yticks([])
    # plot filter channel in grayscale
    ax.imshow(feature_maps[0,:,:,ix], cmap='gray')
    ix += 1
# show the figure
pyplot.show()

In [ ]:
# image after second convolution

from keras.models import Model
from matplotlib import pyplot

alz = Model(inputs=model.inputs, outputs=model.layers[3].output)

fig, axes = plt.subplots(4,8,figsize=(20, 8))
axes = axes.flatten()

# get feature map for first hidden layer
feature_maps = alz.predict(images)
# plot all 64 maps in an 8x8 squares
ix = 0
for ax in axes:
    # specify subplot and turn of axis
    ax.set_xticks([])
    ax.set_yticks([])
    # plot filter channel in grayscale
    ax.imshow(feature_maps[0,:,:,ix], cmap='gray')
    ix += 1
# show the figure
pyplot.show()

In [ ]:
# image after third convolution

from keras.models import Model
from matplotlib import pyplot

alz = Model(inputs=model.inputs, outputs=model.layers[5].output)

fig, axes = plt.subplots(4,8,figsize=(20, 8))
axes = axes.flatten()

# get feature map for first hidden layer
feature_maps = alz.predict(images)
# plot all 64 maps in an 8x8 squares
ix = 0
for ax in axes:
 # specify subplot and turn of axis
 ax.set_xticks([])
 ax.set_yticks([])
 # plot filter channel in grayscale
 ax.imshow(feature_maps[0,:,:,ix], cmap='gray')
 ix += 1
# show the figure
pyplot.show()